In [1]:
import os
import numpy as np
import pandas as pd
import pickle
import quandl #where quant data comes from
from datetime import datetime
import warnings
warnings.filterwarnings('ignore')

In [2]:
import plotly
import plotly.offline as py
import plotly.graph_objs as go
from plotly.subplots import make_subplots
import plotly.figure_factory as ff
py.init_notebook_mode(connected=True)

### Retriving Bitcoin data thru API 
First we get data by using API.

In [3]:
f = open("access.txt", "r")
access = f.read()
quandl.ApiConfig.api_key = access

In [4]:
def get_quandl_data(quandl_id):
    '''Download and cache Quandl dataseries'''
    cache_path = '{}.pkl'.format(quandl_id).replace('/','-')
    try:
        f = open(cache_path,'rb')
        df = pickle.load(f)
        print('Loaded {} from cache'.format(quandl_id))
    except(OSError,IOError)as e:
        print('Downloading {} from Quandl'.format(quandl_id))
        df = quandl.get(quandl_id,returns = 'pandas')
        df.to_pickle(cache_path)
        print('Cacheed {} at {}'.format(quandl_id,cache_path))
    return df

Here in the code we using `pickle` to serialize and save the downloaded data as a file, which will prevent the script from re-downloading the same data each time run the script. The function return the data as a pd dataframe.

In [5]:
# pull the historical btc exchange rate for the kraken btc exchange
btc_usd_price_kraken = get_quandl_data('BCHARTS/KRAKENUSD')

Loaded BCHARTS/KRAKENUSD from cache


In [6]:
btc_usd_price_kraken.tail()

Open     High      Low    Close  Volume (BTC)  \
Date                                                           
2021-06-16  40167.3  40493.0  38120.0  38337.1   6487.206888   
2021-06-17  38337.1  39561.4  37405.0  38078.2   6003.220618   
2021-06-18  38078.2  38193.1  35126.0  35824.0   6558.468890   
2021-06-19  35824.0  36450.0  34901.0  35490.5   4485.076656   
2021-06-20  35484.2  36112.2  33370.0  35668.7   6229.513564   

            Volume (Currency)  Weighted Price  
Date                                           
2021-06-16       2.539206e+08    39141.737747  
2021-06-17       2.307246e+08    38433.468618  
2021-06-18       2.409217e+08    36734.445103  
2021-06-19       1.603145e+08    35743.971502  
2021-06-20       2.168125e+08    34804.086189

In [7]:
# chart rh btc priding data
btc_trace = go.Scatter(x=btc_usd_price_kraken.index, y = btc_usd_price_kraken['Weighted Price'])
py.iplot([btc_trace])

### Get the price data from more BTC exchange
Since there are some hitch in the dataset, we don't want them to impact the result of our analysis, so we need to import the data from other exchange markets and fill out the spikes.

In [8]:
exchanges = ['COINBASE', 'BITSTAMP','ITBIT','EXCHB','CBX','Btctree']
exchange_data = {}
exchange_data['KRAKEN'] = btc_usd_price_kraken

for item in exchanges:
    exchange_code = 'BCHARTS/{}USD'.format(item)
    exchange_data[item] = get_quandl_data(exchange_code)

Loaded BCHARTS/COINBASEUSD from cache
Loaded BCHARTS/BITSTAMPUSD from cache
Loaded BCHARTS/ITBITUSD from cache
Loaded BCHARTS/EXCHBUSD from cache
Loaded BCHARTS/CBXUSD from cache
Loaded BCHARTS/BtctreeUSD from cache


In [9]:
def merge_dfs(dfs,labels,col):
    '''merge the dataframes on columns'''
    series = {}
    for index in range(len(dfs)):
        series[labels[index]]= dfs[index][col]
    return pd.DataFrame(series)

btc_usd = merge_dfs(list(exchange_data.values()),list(exchange_data.keys()),'Weighted Price')

In [11]:
btc_usd.tail()

KRAKEN  COINBASE      BITSTAMP  ITBIT  EXCHB  CBX  Btctree
Date                                                                        
2021-06-16  39141.737747       NaN  39266.920444    NaN    NaN  NaN      NaN
2021-06-17  38433.468618       NaN  38449.364210    NaN    NaN  NaN      NaN
2021-06-18  36734.445103       NaN  36802.295855    NaN    NaN  NaN      NaN
2021-06-19  35743.971502       NaN  35743.751401    NaN    NaN  NaN      NaN
2021-06-20  34804.086189       NaN  34791.393581    NaN    NaN  NaN      NaN

After filling out the gaps in the dataset, we try to plot the data first, now these data shown below are from four different exchange markets.

In [12]:
def df_scatter(df,title,separate_y_axis = False, y_axis_label='', scale = 'linear',initial_hide =False):
    '''generate a scatter plot of the entire dataframe
    There might be problms with plotly version >= 3.0.0. downgrade to 2.7.0 will fix the issue
    '''
    label_arr = list(df)
    series_arr = list(map(lambda col:df[col],label_arr))
    
    layout = go.Layout(
        title = title,legend = dict(orientation = 'h'),xaxis=dict(type='date'),
        yaxis = dict(title=y_axis_label,showticklabels=not separate_y_axis,
                    type=scale)
    )
    y_axis_config = dict(overlaying='y',showticklabels=False,type=scale)
    visibility = True
    if initial_hide:
        visibility = 'legendonly'
    # form trace for each series
    trace_arr = []
    for index,series in enumerate(series_arr):
        trace = go.Scatter(x=series.index,y=series,
                           name=label_arr[index],visible = visibility)
        # Add separate axis for the series
        if separate_y_axis:
            trace['yaxis'] = 'y{}'.format(index + 1)
            layout['yaxis{}'.format(index+1)]=y_axis_config
        trace_arr.append(trace)
    
    fig = go.Figure(data=trace_arr,layout = layout)
    py.iplot(fig)
    
df_scatter(btc_usd,'Bitcoin Price (USD) by Exchange')

### Do further data cleaning 

The goal is to remove all the 0's in the dataset to make sure the precision of the analysis, since the bitcoin price never has 0 as its value.

In [13]:
btc_usd.replace(0,np.nan,inplace=True)

In [14]:
# plot again
df_scatter(btc_usd,'Bitcoin Price (USD) by Exchange')

#### Average prices  

After removing all the 0s in the dataset, now we calculate the average price for each cryptocurrency for later use.

In [15]:
# add a new col to calculate the avg of the prices
btc_usd['avg_btc'] = btc_usd.mean(axis=1)

In [16]:
btc_trace = go.Scatter(x=btc_usd.index, y = btc_usd['avg_btc'])
py.iplot([btc_trace])

### Retrive Altcoin price data  

Our ultimate goal is to find out the relationships between the different currencies, and then to decide what to do next based on the results.

In [17]:
def get_json_data(url,cache_path):
    '''Download and cache json data and return a dataframe'''
    try:
        f = open(cache_path,'rb')
        df = pickle.load(f)
        print('Loaded {} from cache'.format(url))
    except(OSError,IOError)as e:
        print('Downloading {} from Quandl'.format(url))
        df = pd.read_json(url)
        df.to_pickle(cache_path)
        print('Cached response at {}'.format(url,cache_path))
    return df

In [18]:
base_polo_url = "https://poloniex.com/public?command=returnChartData&currencyPair={}&start={}&end={}&period={}"
start_date = datetime.strptime('2015-01-01','%Y-%m-%d')
end_date = datetime.now()
period = 86400 # 86400s per day

def get_crypto_data(poloniex):
    url = base_polo_url.format(poloniex,start_date.timestamp(),end_date.timestamp(),period)
    data_df = get_json_data(url,poloniex)
    data_df = data_df.set_index('date')
    return data_df
    

In [19]:
altcoins = ['ETH', 'LTC','ETC','STR','DASH','SC','XEM','DOGE']
alt_data = {}
for coin in altcoins:
    coinpair = 'BTC_{}'.format(coin)
    alt_data[coin] = get_crypto_data(coinpair)

Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_ETH&start=1420099200.0&end=1643235660.64227&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_LTC&start=1420099200.0&end=1643235660.64227&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_ETC&start=1420099200.0&end=1643235660.64227&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_STR&start=1420099200.0&end=1643235660.64227&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_DASH&start=1420099200.0&end=1643235660.64227&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_SC&start=1420099200.0&end=1643235660.64227&period=86400 from cache
Loaded https://poloniex.com/public?command=returnChartData&currencyPair=BTC_XEM&start=1420099200.0&end=1643235660.64227&period=86400 fro

In [20]:
display(alt_data['ETH'].tail())
display(alt_data['DOGE'].tail())

high       low      open     close      volume  quoteVolume  \
date                                                                          
2022-01-22  0.071636  0.067319  0.070405  0.068786  397.300104  5755.402107   
2022-01-23  0.070816  0.068292  0.068773  0.070061  111.459195  1605.011897   
2022-01-24  0.070069  0.064662  0.070049  0.066555  462.793411  6964.619802   
2022-01-25  0.067059  0.065604  0.066559  0.066507   98.907554  1491.796247   
2022-01-26  0.066777  0.065576  0.066516  0.066164   40.575233   613.237688   

            weightedAverage  
date                         
2022-01-22         0.069031  
2022-01-23         0.069444  
2022-01-24         0.066449  
2022-01-25         0.066301  
2022-01-26         0.066166

high       low      open     close     volume   quoteVolume  \
date                                                                          
2022-01-22  0.000004  0.000004  0.000004  0.000004  70.446946  1.900258e+07   
2022-01-23  0.000004  0.000004  0.000004  0.000004  39.391607  1.007522e+07   
2022-01-24  0.000004  0.000004  0.000004  0.000004  33.825733  8.859177e+06   
2022-01-25  0.000004  0.000004  0.000004  0.000004  32.453708  8.358563e+06   
2022-01-26  0.000004  0.000004  0.000004  0.000004   7.314291  1.885755e+06   

            weightedAverage  
date                         
2022-01-22         0.000004  
2022-01-23         0.000004  
2022-01-24         0.000004  
2022-01-25         0.000004  
2022-01-26         0.000004

### Convert price in USD
We now have crypto-btc, and btc-usd, we could have crypto-usd, as a more convinient way in terms of understanding the data by taking logs to the data value.

In [21]:
for coin in alt_data.keys():
    alt_data[coin]['price_usd'] = alt_data[coin]['weightedAverage']*btc_usd['avg_btc']


In [22]:
combined_df = merge_dfs(list(alt_data.values()),list(alt_data.keys()),'price_usd')
combined_df['BTC'] = btc_usd['avg_btc']

In [23]:
df_scatter(combined_df, 'Cryptocurrency Prices (USD)',separate_y_axis = False, 
           y_axis_label = 'Coin Value (USD)',scale = 'log') # if not using log scale, the plot would look very diverse.

### Figure out the relationships between the cryptocurrencies  

Here we want to dig some more insights from the dataset between the cryptocurrencies.  
It's time to do the corellation analysis among the cryptocurrencies. 
There are similar fluctuations appear along the timeline, thus we could use corr() in pandas to do the correlation analysis, which computes the pearson correlation coefficient for each col in the dataframe.  
Compute correlations directly on a non-stationary time series can give biased corr values. We will work around it by using `pct_change()` method, which will convert each cell in the dataframe from an absolute price value to a daily return percentage.

In [24]:
combined_df_16 = combined_df[combined_df.index.year==2016]
combined_df_17 = combined_df[combined_df.index.year==2017]
combined_df_18 = combined_df[combined_df.index.year==2018]
combined_df_19 = combined_df[combined_df.index.year==2019]
combined_df_20 = combined_df[combined_df.index.year==2020]
combined_df_21 = combined_df[combined_df.index.year==2021]

combined_df_21.pct_change().corr(method ='pearson')

ETH       LTC       ETC       STR      DASH        SC       XEM  \
ETH   1.000000  0.835335  0.550980  0.695266  0.674886  0.552123  0.515511   
LTC   0.835335  1.000000  0.681719  0.735313  0.761632  0.612676  0.534197   
ETC   0.550980  0.681719  1.000000  0.546896  0.666843  0.515909  0.422660   
STR   0.695266  0.735313  0.546896  1.000000  0.648455  0.598926  0.546983   
DASH  0.674886  0.761632  0.666843  0.648455  1.000000  0.529396  0.473264   
SC    0.552123  0.612676  0.515909  0.598926  0.529396  1.000000  0.463295   
XEM   0.515511  0.534197  0.422660  0.546983  0.473264  0.463295  1.000000   
DOGE  0.279396  0.312444  0.279885  0.378864  0.257395  0.564827  0.175104   
BTC   0.787422  0.783646  0.454976  0.658979  0.570904  0.571947  0.535565   

          DOGE       BTC  
ETH   0.279396  0.787422  
LTC   0.312444  0.783646  
ETC   0.279885  0.454976  
STR   0.378864  0.658979  
DASH  0.257395  0.570904  
SC    0.564827  0.571947  
XEM   0.175104  0.535565  
DOGE  1.000000  0.355138  
BTC   0.355138  1.000000

In [25]:
# now we need to visualize the correlation matrix by heatmap
def corr_heatmap(df,title,absolute_bound = True):
    heatmap = go.Heatmap(
        z = df.corr(method = 'pearson').as_matrix(),
        x = df.columns,
        y = df.columns,
        colorbar = dict(title = 'Pearson Coeeficient'), colorscale='rdbu'
    )
    layout = go.Layout(title = title,width=800,height=400)
    
    if absolute_bound:
        heatmap['zmax'] = 1.0
        heatmap['zmin'] = -1.0
    
    fig = go.Figure(data = [heatmap],layout = layout)
    py.iplot(fig) 

In [26]:
corr_heatmap(combined_df_21.pct_change(),'Cryptocurrency Correlations in 2021')

In [27]:
corr_heatmap(combined_df_20.pct_change(),'Cryptocurrency Correlations in 2020')

In [28]:
corr_heatmap(combined_df_19.pct_change(),'Cryptocurrency Correlations in 2019')


In [29]:
corr_heatmap(combined_df_16.pct_change(),'Cryptocurrency Correlations in 2016')

Since in the market there are many analysis talking about the relationship between the different crypocurrencies, but some of them don't have data to support their conclusions. Here we are using data and visualization tools to display some straightforward insights from the raw data in the market.
The above process could be considered as a EDA.

The correlations between the cryptocurrencies from 2016 to 2019 is getting more and more stronger.Reasons could be as follows:  

1. more and more attentions to the cryptocurrencies/blockchain  
2. hedging funds also has certain impact on the crypto
...


## What could we do after this?

1. blockchain mining datasets 
2. stocks, commdenities, to see the correlations 
3. train a ml model to predict price，(CNN, RNN ...) 
4. trading bot, chatting bot  
5. is quant investment making money? (based on the historical data) 